Team Comparisons

In [1]:
import csv
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression

Import Data

In [2]:
Stats = []
with open('TI9.csv', newline = '') as csvfile:
    spamreader = csv.reader(csvfile, delimiter = ',', quotechar='|')
    for row in spamreader:
        Stats.append(row)

Games Array

In [3]:
Team1 = []
Team2 = []
Winner = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        Team1.append(Stats[i][1])
        Team2.append(Stats[i][4])
        Winner.append(Stats[i][7])
        i += 1       

Total Wins per team

In [4]:
Teamlist = ['OG','Team Liquid', 'PSG.LGD','Team Secret','Vici Gaming','Evil Geniuses','Royal Never Give Up','Infamous Gaming', 'Newbee', 'TNC Predator','Virtus.pro','Fnatic','Alliance','Mineski','Natus Vincere', 'Chaos Esports Club', 'KEEN GAMING', 'Ninjas in Pyjamas']


wij = np.zeros((len(Teamlist), len(Teamlist)))


wincounts = []
for x in Teamlist:
    wincounts.append(Winner.count(x))

Wins i vs j matrix

In [5]:
binWins = np.zeros(len(Winner))
for i in range(len(Winner)):
    if Winner[i] == Team1[i]:
        binWins[i] = 1

d = {'Radiant':Team1, 'Dire':Team2, 'Winner':binWins}

index_dict = {'OG':0,'Team Liquid':1,'PSG.LGD':2,'Team Secret':3,'Vici Gaming':4,'Evil Geniuses':5,'Royal Never Give Up':6,'Infamous Gaming':7,'Newbee':8,'TNC Predator':9,'Virtus.pro':10,'Fnatic':11,'Alliance':12,'Mineski':13,'Natus Vincere':14,'Chaos Esports Club':15,'KEEN GAMING':16,'Ninjas in Pyjamas':17}

games = pd.DataFrame(data = d)

Wi = pd.DataFrame(np.array([wincounts]), columns = Teamlist)
    
np.array(wincounts)


for n in range(len(games.loc[:,'Radiant'])):
    i = games.loc[n,'Radiant']
    j = games.loc[n,'Dire']
    if games.loc[n,'Winner'] == i:
        wij[index_dict[i],index_dict[j]] += 1
    else:
        wij[index_dict[j],index_dict[i]] += 1

To implement the Bradley Terry Model as a GLM we will be relying on the logistic model for binomially distributed data as implemented by Jamil, 2010 such that logit(p_(i>j))= log(p_(i>j)/(1-p_(i>j)) = lamda_i - lambda_j


Model Matrix

From here we should be able to apply the logit model as we have pij, X and unknowns lambda where
logit[pij] = X*Lambda

Our inputs are clearly 2 teams with an output vector as 0 or 1 depending whether team 1 or team 2 wins

Lets do some quick Data fixing on our existing design and response matrixes

In [6]:
"""Number of teams"""
k = len(Teamlist)
N = len(Winner)
X = np.zeros((N,k))


def designMatrix(data, index_dict):
    """ Creates a design matrix for standard Bradley Terry Model"""
    N = len(data.index)
    k = len(index_dict.keys())
    X = np.zeros((N,k))
    gameNumber = 0
    for index, row in data.iterrows():
        X[gameNumber][index_dict[row[0]]] = 1
        X[gameNumber][index_dict[row[1]]] = -1
        gameNumber +=1
    return(X)

gameNumber = 0
for index, row in games.iterrows():
    X[gameNumber][index_dict[row['Radiant']]] = 1
    X[gameNumber][index_dict[row['Dire']]] = -1
    gameNumber+= 1
    
def BTfit(X, Y, Teamlist, tol):
    N = len(Y)
    k = len(Teamlist)
    X = np.matrix(X)
    Xt = np.matrix.transpose(X)
    XXt = np.dot(X,Xt)
    Y = np.matrix(Y)
    Y = np.matrix.transpose(Y)
    rankings = np.matrix(np.random.rand(k,1))
    tol = 1
    t = 0
    while tol > 0.00001:
        p = np.exp(np.dot(X,rankings))/(1+np.exp(np.dot(X,rankings)))
        gradient = np.matrix(np.zeros((1,k)))
        hessian = 0
        for i in range(N):
            gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
            hessian += XXt.item((i,i))*p[i]*(1-p[i])
    
        
        oldrankings = np.matrix.transpose(rankings)
        rankings = oldrankings + (1/hessian)*gradient
    
        tol = np.dot(rankings-oldrankings, np.matrix.transpose(rankings-oldrankings))
        rankings = np.matrix.transpose(rankings)
        
    ranks = np.asarray(rankings)
    ranks = np.ndarray.tolist(ranks)
    data = {"Teams":Teamlist, "Ranks":ranks}
    Teamskills = pd.DataFrame(data)
    return(Teamskills)
    
test = designMatrix(games, index_dict)
test2 = BTfit(test, binWins, Teamlist,1)
print(test2)
    
X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(binWins)
Y = np.matrix.transpose(Y)
rankings = np.matrix(np.random.rand(k,1))
tol = 1.


                  Teams                   Ranks
0                    OG      [2.25569281109922]
1           Team Liquid    [1.2128625066173264]
2               PSG.LGD    [1.8909255343557532]
3           Team Secret    [1.2833834586072261]
4           Vici Gaming    [0.8680274464421075]
5         Evil Geniuses    [0.7536658535368154]
6   Royal Never Give Up   [0.12056848452335495]
7       Infamous Gaming    [0.2584829093573106]
8                Newbee    [0.6237124619241472]
9          TNC Predator    [0.6354337537038568]
10           Virtus.pro   [0.04881648194085936]
11               Fnatic   [0.04995648152497397]
12             Alliance   [0.49697482060111675]
13              Mineski    [0.7093699957729003]
14        Natus Vincere   [0.02457553418378923]
15   Chaos Esports Club   [-0.7531475058296778]
16          KEEN GAMING  [-0.24346696071855753]
17    Ninjas in Pyjamas    [-1.000884034807416]


In [7]:
while tol > 0.00001:
    p = np.exp(np.dot(X,rankings))/(1+np.exp(np.dot(X,rankings)))
    gradient = np.matrix(np.zeros((1,k)))
    hessian = 0
    for i in range(N):
        gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
        hessian += XXt.item((i,i))*p[i]*(1-p[i])
        
    oldrankings = np.matrix.transpose(rankings)
    rankings = oldrankings + (1/hessian)*gradient
    
    tol = np.dot(rankings-oldrankings, np.matrix.transpose(rankings-oldrankings))
    rankings = np.matrix.transpose(rankings)

Hero Ratings

In [8]:
heroes1 = []
heroes2 = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        heroes1.append(Stats[i][2])
        heroes2.append(Stats[i][5])
        i += 1   

In [9]:
heroes1

['Io  Tiny  Abaddon  Timbersaw  Gyrocopter',
 'Rubick  Tidehunter  Ogre Magi  Templar Assassin  Juggernaut',
 'Tidehunter  Templar Assassin  Shadow Shaman  Lifestealer  Enigma',
 'Tidehunter  Chen  Rubick  Templar Assassin  Meepo',
 'Elder Titan  Rubick  Faceless Void  Shadow Fiend  Dark Seer',
 'Elder Titan  Rubick  Sven  Dark Seer  Templar Assassin',
 'Tiny  Faceless Void  Mirana  Tinker  Shadow Demon',
 'Elder Titan  Rubick  Magnus  Wraith King  Bristleback',
 'Chen  Tidehunter  Earth Spirit  Leshrac  Meepo',
 'Chen  Alchemist  Tidehunter  Rubick  Legion Commander',
 'Shadow Demon  Sand King  Jakiro  Sven  Dragon Knight',
 "Elder Titan  Faceless Void  Pangolier  Nature's Prophet  Zeus",
 'Tiny  Omniknight  Windranger  Crystal Maiden  Bristleback',
 'Leshrac  Tidehunter  Lion  Earth Spirit  Medusa',
 'Elder Titan  Alchemist  Rubick  Ember Spirit  Dark Seer',
 'Mirana  Ogre Magi  Tidehunter  Faceless Void  Tinker',
 'Tiny  Faceless Void  Witch Doctor  Enigma  Abaddon',
 'Magnus  Shado

Firstly we need to count comparative wins separately, then we will compare them as a team

In [10]:
heroes1new = []
heroes2new = []
for i in heroes1:
    heroes1new.append(i.split("  "))

for i in heroes2:
    heroes2new.append(i.split("  "))

In [11]:
#Herodict goes here
l = 0
hdict = {}
for i in heroes1new:
    for j in i:
        if j in hdict:
            continue
        else:
            hdict[j] = l
            l += 1

for i in heroes2new:
    for j in i:
        if j in hdict:
            continue
        else:
            hdict[j] = l
            l += 1
hdict

{'Io': 0,
 'Tiny': 1,
 'Abaddon': 2,
 'Timbersaw': 3,
 'Gyrocopter': 4,
 'Rubick': 5,
 'Tidehunter': 6,
 'Ogre Magi': 7,
 'Templar Assassin': 8,
 'Juggernaut': 9,
 'Shadow Shaman': 10,
 'Lifestealer': 11,
 'Enigma': 12,
 'Chen': 13,
 'Meepo': 14,
 'Elder Titan': 15,
 'Faceless Void': 16,
 'Shadow Fiend': 17,
 'Dark Seer': 18,
 'Sven': 19,
 'Mirana': 20,
 'Tinker': 21,
 'Shadow Demon': 22,
 'Magnus': 23,
 'Wraith King': 24,
 'Bristleback': 25,
 'Earth Spirit': 26,
 'Leshrac': 27,
 'Alchemist': 28,
 'Legion Commander': 29,
 'Sand King': 30,
 'Jakiro': 31,
 'Dragon Knight': 32,
 'Pangolier': 33,
 "Nature's Prophet": 34,
 'Zeus': 35,
 'Omniknight': 36,
 'Windranger': 37,
 'Crystal Maiden': 38,
 'Lion': 39,
 'Medusa': 40,
 'Ember Spirit': 41,
 'Witch Doctor': 42,
 'Silencer': 43,
 'Phantom Lancer': 44,
 'Riki': 45,
 'Ancient Apparition': 46,
 'Arc Warden': 47,
 'Centaur Warrunner': 48,
 'Enchantress': 49,
 'Invoker': 50,
 'Earthshaker': 51,
 'Oracle': 52,
 'Terrorblade': 53,
 'Lina': 54,
 '

Now to try and break down all possible matchups (which is a fuckload)

In [12]:
Matchups1 = []
binWins2 = []
for i in heroes1new:
    for j in i:
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)


Matchups2 = []
for i in heroes2new:
    for j in range(5):
        Matchups2.append(i[0])
        Matchups2.append(i[1])
        Matchups2.append(i[2])
        Matchups2.append(i[3])
        Matchups2.append(i[4])

    
for i in binWins:
    for j in range(25):
        binWins2.append(i)

d = {'Radiant':Matchups1, 'Dire':Matchups2, 'Winner':binWins2}
heroGames = pd.DataFrame(data = d)


In [13]:
"""Number of Heroes"""
k = len(hdict.keys())
""" Number of Comparisons """
N = len(binWins2)
""" Design Matrix """
X = np.zeros((N,k))
gameNumber = 0
for index, row in heroGames.iterrows():
    X[gameNumber][hdict[row['Radiant']]] = 1
    X[gameNumber][hdict[row['Dire']]] = -1
    gameNumber+= 1
test3 = designMatrix(heroGames, hdict)    

X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(binWins2)
Y = np.matrix.transpose(Y)
rankings = np.matrix(np.random.rand(k,1))
tol = 1.


In [14]:
ranks = np.asarray(rankings)
ranks = np.ndarray.tolist(ranks)

heroes = []
for i in hdict.keys():
    heroes.append(i)
    
data = {"Heroes":heroes, "Ranks":ranks}
data
Heroskills = pd.DataFrame(data)
Heroskills

test4 = BTfit(test3, binWins2, heroes,1)

Lets do some data fixing now on rankings and our two data frames

In [15]:
Heroskills = Heroskills.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [16]:
heroes = []
for i in hdict.keys():
    heroes.append(i)

How do we interpret the 2 ratings, for teams it is clear, but for heroes i imagine we can add up the skills of both teams and treat them as a single team, to test

for treating heroes as players in a team we refer back to Haziq

We shall first implement this for team OG, haziq does this for liverpool and we will implement this in a similar way, what is worth noting for the final potential model is that in the EPL model there are no shared players while in ours "players" will predominantly be shared

From Huang et al. 2006

In [17]:
""" Consider k individuals """
k = len(hdict.keys())
k

115

In [18]:
for i in heroes1new:
    i.sort()

In [19]:
I = []
for i in heroes1new:
    l = 0
    for j in heroes1new:
        if l == 0:
            continue
        elif i == j:
            print(True)
        l+=1
    for j in heroes2new:
        if i ==j:
            print(True)

In [20]:
ri = binWins
herodf = pd.DataFrame(data = {"Radiant": heroes1new, "Dire": heroes2new, "Winner":binWins})

In [21]:
q = np.zeros(len(hdict.keys()))
qplus = np.zeros(len(hdict.keys()))
qminus = np.zeros(len(hdict.keys()))
game = 0
for hero in hdict.keys():
    for i in range(len(binWins)):
        if hero in herodf["Radiant"][i]:
            if herodf["Winner"][i] == 1:
                q[hdict[hero]] += 1
                qplus[hdict[hero]] += 1
        elif hero in herodf["Dire"][i]:
            if herodf["Winner"][i] == 0:
                q[hdict[hero]] += 1
                qminus[hdict[hero]] += 1
        else:
            continue

In [22]:
qminus

array([ 9., 15.,  4.,  2., 15., 12., 16., 13.,  6.,  2.,  4., 13.,  6.,
        8.,  1., 27.,  9.,  2.,  2., 10., 14.,  1., 25.,  5.,  7.,  4.,
        4., 13.,  7.,  3., 13.,  4.,  4.,  4.,  1.,  0.,  5.,  7., 10.,
        7.,  3.,  9.,  4.,  0.,  1.,  0.,  7.,  2., 10., 11.,  7., 11.,
        3.,  1.,  7.,  1.,  5.,  2., 14.,  4.,  0.,  4.,  0.,  0.,  4.,
        8.,  2.,  2.,  5.,  8.,  1.,  4.,  2.,  3.,  2.,  2.,  1.,  1.,
        4.,  1.,  1.,  8.,  2.,  0.,  3.,  0.,  2.,  4.,  4.,  0.,  4.,
        0.,  0.,  0.,  0.,  1.,  1.,  2.,  0.,  3.,  0.,  0.,  6.,  0.,
        0.,  1.,  5.,  0.,  1.,  0.,  1.,  1.,  0.,  0.,  0.])

In [78]:
k = len(hdict.keys())
m = len(binWins)
Ip = np.zeros((m,k))
I = np.zeros((m,k))
l = 0
r = binWins
for i in heroes1new:
    for j in i:
        if binWins[l] == 1:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
        l+=1
        
    l = 0
for i in heroes2new:
    for j in i:
        if binWins[l] == 0:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l += 1
    
po = np.ones(k)/k
maxiter = 1000;
delta = np.zeros(k)

def newI(team1,team2, k, m, index_dict):
    I = np.zeros((m,k))
    l = 0
    
    for i in team1:
        for j in i:
            I[l,index_dict[j]] = 1
        l += 1
    l = 0
    for i in team2:
        for j in i:
            I[l,index_dict[j]] = 1
        l += 1
    return(I)

def newIp(team1, k, m, index_dict):
    Ip =np.zeros((m,k))
    l = 0
    for i in team1:
        for j in i:
            Ip[l,index_dict[j]] = 1
        l+=1
    return(Ip)

def BTfit2(I,Ip,r,k,maxiter,playerlist):
    po = np.random.rand(k)
    delta = np.zeros(k)
    for t in range(maxiter):
        for i in range(k):
            pp = np.tile(np.transpose(po), (r.size,1))
            qp = np.sum(np.multiply(pp,Ip),axis=1)
            Ipp = Ip[:,i]
            q = np.sum(np.multiply(pp,I),axis=1)
            Ii = I[:,i]
            Ipp = Ipp.astype(int)
            Ii = Ii.astype(int)
            delta[i] = np.sum(np.divide(r[Ipp],qp[Ipp]))/np.sum(np.divide(r[Ii],q[Ii]))
            if np.isnan(delta[i]):
                print(po)
                print(delta)
                print(qp[Ipp])
                print(q[Ii])
                break
            po[i] = delta[i]*po[i]
            po = po/np.sum(po)
        if np.max(np.abs(delta-1)) < 0.001:
            separate = t*k
            break
    pest = po
    data = {"Heroes":playerlist, "Ranks":pest}
    Heroskills2 = pd.DataFrame(data)
    return(Heroskills2)
    
    
    
    
for t in range(maxiter):
    for i in range(k):
        pp = np.tile(np.transpose(po), (binWins.size,1))
        qp = np.sum(np.multiply(pp,Ip),axis=1)
        Ipp = Ip[:,i]
        q = np.sum(np.multiply(pp,I),axis=1)
        Ii = I[:,i]
        Ipp = Ipp.astype(int)
        Ii = Ii.astype(int)
        delta[i] = np.sum(np.divide(r[Ipp],qp[Ipp]))/np.sum(np.divide(r[Ii],q[Ii]))
        if np.isnan(delta[i]):
            print(po)
            print(delta)
            print(qp[Ipp])
            print(q[Ii])
            break
        po[i] = delta[i]*po[i]
        po = po/np.sum(po)
    if np.max(np.abs(delta-1)) < 0.001:
        separate = t*k
        break
pest = po                        
        
        
test5 = BTfit2(I,Ip,binWins,k,10,heroes)
test5


Heroes     Ranks
0                  Io  0.009305
1                Tiny  0.015940
2             Abaddon  0.012790
3           Timbersaw  0.007418
4          Gyrocopter  0.007593
5              Rubick  0.007991
6          Tidehunter  0.015120
7           Ogre Magi  0.035343
8    Templar Assassin  0.009662
9          Juggernaut  0.013965
10      Shadow Shaman  0.002720
11        Lifestealer  0.000947
12             Enigma  0.013490
13               Chen  0.013671
14              Meepo  0.000299
15        Elder Titan  0.013781
16      Faceless Void  0.008429
17       Shadow Fiend  0.008025
18          Dark Seer  0.000629
19               Sven  0.018135
20             Mirana  0.014894
21             Tinker  0.009890
22       Shadow Demon  0.021991
23             Magnus  0.014409
24        Wraith King  0.001446
25        Bristleback  0.003469
26       Earth Spirit  0.004348
27            Leshrac  0.015714
28          Alchemist  0.007822
29   Legion Commander  0.011316
..                ...       ...
85        Drow Ranger  0.001731
86      Skywrath Mage  0.006247
87        Dark Willow  0.012972
88         Naga Siren  0.012885
89            Undying  0.007833
90            Spectre  0.007047
91              Pudge  0.010083
92             Clinkz  0.003054
93        Bloodseeker  0.011482
94       Chaos Knight  0.005081
95              Viper  0.000248
96               Bane  0.013623
97            Slardar  0.008785
98             Huskar  0.006543
99      Troll Warlord  0.009708
100        Lone Druid  0.007322
101   Vengeful Spirit  0.013838
102  Treant Protector  0.006603
103            Dazzle  0.000970
104         Disruptor  0.007631
105           Phoenix  0.009200
106              Tusk  0.013409
107              Luna  0.005025
108              Doom  0.003372
109             Lycan  0.001178
110    Spirit Breaker  0.005879
111     Night Stalker  0.005337
112     Bounty Hunter  0.000379
113        Venomancer  0.008850
114      Ember Spirit  0.008674

[115 rows x 2 columns]

Start with initial p_j^0 > 0, j = 1,...,k and obtain corresponding qi's values for i = 1,...,m
k = no.heros
m = no.games



In [24]:
pest/np.min(pest)

array([4.15664897e+09, 1.41287231e+33, 5.33880590e+11, 3.99665343e+11,
       4.88251635e+30, 1.96090336e+22, 1.65747722e+20, 2.96461388e+51,
       1.19650899e+07, 2.54963297e+16, 5.26780997e+11, 2.95649552e+51,
       1.63430311e+19, 9.51048945e+11, 2.01538297e+02, 2.54002755e+41,
       1.25849115e+12, 1.74403607e+09, 1.96198420e+02, 1.06117961e+22,
       1.80841981e+25, 3.71407042e+04, 2.30092479e+58, 1.23375512e+19,
       1.14492409e+07, 9.61707643e+06, 5.84230717e+11, 3.88779057e+43,
       7.62887277e+11, 8.28408963e+13, 8.88777828e+24, 3.56096971e+16,
       4.22955878e+04, 2.88548941e+16, 7.18560061e+06, 3.19806179e+04,
       1.39308225e+14, 1.28617477e+07, 1.12159925e+22, 3.28002371e+09,
       4.38726091e+04, 8.39145507e+21, 2.30155883e+09, 6.46071095e+13,
       1.46344116e+09, 1.89703843e+02, 4.79795770e+21, 2.05132107e+02,
       3.65391315e+24, 5.50679359e+14, 9.58072809e+11, 1.75960621e+27,
       2.00996632e+09, 7.73804043e+06, 1.40214435e+24, 7.73804043e+06,
      

In [81]:
data = {"Heroes":heroes, "Ranks":pest}
data
Heroskills2 =test5
Heroskills2

Heroes     Ranks
0                  Io  0.009305
1                Tiny  0.015940
2             Abaddon  0.012790
3           Timbersaw  0.007418
4          Gyrocopter  0.007593
5              Rubick  0.007991
6          Tidehunter  0.015120
7           Ogre Magi  0.035343
8    Templar Assassin  0.009662
9          Juggernaut  0.013965
10      Shadow Shaman  0.002720
11        Lifestealer  0.000947
12             Enigma  0.013490
13               Chen  0.013671
14              Meepo  0.000299
15        Elder Titan  0.013781
16      Faceless Void  0.008429
17       Shadow Fiend  0.008025
18          Dark Seer  0.000629
19               Sven  0.018135
20             Mirana  0.014894
21             Tinker  0.009890
22       Shadow Demon  0.021991
23             Magnus  0.014409
24        Wraith King  0.001446
25        Bristleback  0.003469
26       Earth Spirit  0.004348
27            Leshrac  0.015714
28          Alchemist  0.007822
29   Legion Commander  0.011316
..                ...       ...
85        Drow Ranger  0.001731
86      Skywrath Mage  0.006247
87        Dark Willow  0.012972
88         Naga Siren  0.012885
89            Undying  0.007833
90            Spectre  0.007047
91              Pudge  0.010083
92             Clinkz  0.003054
93        Bloodseeker  0.011482
94       Chaos Knight  0.005081
95              Viper  0.000248
96               Bane  0.013623
97            Slardar  0.008785
98             Huskar  0.006543
99      Troll Warlord  0.009708
100        Lone Druid  0.007322
101   Vengeful Spirit  0.013838
102  Treant Protector  0.006603
103            Dazzle  0.000970
104         Disruptor  0.007631
105           Phoenix  0.009200
106              Tusk  0.013409
107              Luna  0.005025
108              Doom  0.003372
109             Lycan  0.001178
110    Spirit Breaker  0.005879
111     Night Stalker  0.005337
112     Bounty Hunter  0.000379
113        Venomancer  0.008850
114      Ember Spirit  0.008674

[115 rows x 2 columns]

Compare these results to overall pick rate, and how it changes over time as the model begins to converge

Cool, so we've implemented two models for hero weighting, likely should implement the combined model now, additionally should place these into functions so that we can develop train/test data for analytics

Combined Model: The idea behind the comparative model is to treat the heroes picked in the game as a homeground advantage by seeing which composition has the highest win-probability according to previous model (sum of player skills is the teams skill independent of which team is playing) additionally there is likely ways to treat it as a second logistic parameter but ya boi dumb so...

Imma do this with directly optimizing the log likelihood cause i a lazy bitch

In [82]:
"aij be the number of times i beats j at home"
k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(binWins)

def BTloglik(li):
    lilj = np.zeros(len(li[:-1]))
    for i in range(len(li[:-1])):
        for j in range(len(li[:-1])):
            if i != j:
                lilj[i] += (li[-1]*li[i]+li[j])
    print(lilj)
    ll = c*np.log(li[-1]) + np.sum(np.multiply(wincounts,np.log(li[:-1])))-np.sum(np.multiply(nij,np.log(lilj)))
    return(-ll)

x0 = np.random.rand(k+1)
len(x0[:-1])
wincounts
#np.multiply(Wi,x0[:-2])
BTloglik(x0)


[11.56313333 10.38089908  8.88464286 12.23457577 11.78637053  9.44716589
 10.0002691  11.11766508 10.19403866  9.41283527  9.49252983 12.08060187
  9.91523014 11.02110439 10.52947027 10.36900822 12.13586008 11.42408286]


780.3992680211497

In [27]:
from scipy.optimize import minimize

In [28]:
np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

  9.55515222 11.70714082 15.7181992  11.8939733  23.59871891 16.27516343]
[34.33789552 17.64626186 14.13227964 14.94750742 21.79568946 18.64683458
 28.11758731 21.06460178 24.1883778  17.90033738 25.83603956 25.3424782
  9.67292177 11.76140703 15.74713109 12.90106272 23.93175587 16.85384506]
[37.6218492  18.3348357  14.48807821 15.42462281 22.32637443 17.97458748
 28.77587695 19.86373045 24.61873363 16.47928156 26.97135819 24.47794742
  9.41429036 11.62559517 15.87977887 10.35323667 23.43363754 14.7103273 ]
[38.23970082 18.28047483 14.5416065  15.51647553 22.23853517 17.67658107
 28.8973998  20.5498021  24.65479827 15.98402772 27.08957355 23.02513745
  9.35570344 11.57635156 15.86424627 10.04358759 23.16741112 14.18405837]
[38.43014647 18.80252414 14.53877979 15.59890993 22.67362846 17.72884594
 29.16795705 20.12950108 24.67302739 16.30128011 27.43982914 24.27537932
  9.34096844 11.59989899 16.05804896  9.56176805 23.74827196 13.50757557]
[36.98396627 18.14903897 14.39513016 15.2235102

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log



[36.76257012 18.258816   14.41272557 15.33291668 21.99026593 18.1238436
 28.49884672 20.21788797 24.21707601 17.20183197 26.89459804 24.16651461
  9.46560335 11.48082942 15.85535625 11.46842807 23.42695458 15.06172019]
[35.78897528 17.92065898 14.27362098 15.10082857 22.00953449 18.05968084
 28.74406902 20.21765618 24.26305698 17.27162597 26.00343568 24.42765502
  9.54529449 11.653884   15.75485713 11.82874219 23.48885029 16.17375402]
[35.77140926 17.88871911 14.26497541 15.18853741 21.76966259 18.00701965
 27.68411485 20.29009413 23.70513872 17.52931667 26.17395891 24.08847311
  9.54142835 11.60908583 15.75429333 11.90801922 23.11386131 17.10345001]
[36.46446438 18.05306411 14.34120895 15.26433422 21.96014654 17.95176184
 28.14635655 20.21337852 23.99251911 17.16413688 26.4654325  24.19805823
  9.49074536 11.60680845 15.80259326 11.39646282 23.26747125 15.97108093]
[39.32398728 18.67038631 14.65566763 15.6784334  22.13575456 17.92693928
 29.46824588 20.13896939 24.45220862 16.7287629

  8.67711075 10.98505279 15.26833203 11.78693194 19.43828878 11.02117777]
[23.22498575 16.83174127 14.4654098  15.59588809 20.35717752 14.45295891
 32.04607421 19.18544929 19.15858042 13.71177744 24.92174994 14.51393462
  8.39467611 10.75363043 15.11109371 12.1868317  18.12562638 10.09085018]
[26.15553267 17.02624169 14.29926919 15.65719989 20.83304355 14.93497253
 31.37791437 19.52174022 20.8907806  14.4371409  24.96159763 16.48862738
  8.58538666 11.03589145 15.09295006 11.45044332 19.03237719 10.94265495]
[26.35653845 17.03243673 14.39171035 15.47364531 21.02909809 15.17287149
 30.97721212 19.58483449 20.75929496 15.0498945  25.32697545 16.89239981
  8.69354968 11.08330139 15.30023063 12.1681494  19.46030052 12.02108688]
[29.1148444  17.17227579 14.24416972 15.20138212 20.25325513 14.87055557
 29.85785485 18.9854451  19.7748356  14.94540556 25.11148472 16.63092794
  8.66737482 10.90492893 15.16919712 12.26360034 19.31393585 10.01627839]
[28.11081496 16.7646487  14.16527033 15.119476

...

  4.46543012  7.33737497 11.7583696   5.05073907  6.39518571  5.46810204]
[11.73971201 10.56761657  9.62300245  9.54458819  8.2062017   7.08183725
  7.95400702  6.92591229  8.13170465  8.85448002  6.49181867  7.15643174
  4.49815458  7.34640171 11.56937395  5.11539662  6.5401221   5.49910055]
[11.80333303 10.38983362  9.5193464   9.54719142  8.12683596  7.11567487
  8.00273564  6.87019022  7.98945684  8.97439952  6.47422587  7.10029574
  4.50403943  7.39370756 11.45650171  5.16038076  6.62794003  5.57082811]
[11.58462207 10.66863204  9.60878394  9.39342947  8.2365076   6.96243609
  7.66636355  6.96000721  8.08785292  8.52646197  6.62074     6.99897822
  4.48006739  7.25925476 11.60048466  4.97717429  6.48031524  5.48431807]
[11.85992604 10.79521208  9.66090674  9.45889179  8.35450992  7.1492135
  7.58820824  6.86903952  8.17266796  8.8326912   6.51584521  7.29362478
  4.47912178  7.32307958 11.77608136  5.00844101  6.41138734  5.44295506]
[11.58474519 10.60726093  9.64050698  9.5503822

[11.49364278 10.55882312  9.63500114  9.45491991  7.97413682  7.04031769
  7.74399602  6.67596521  7.93265841  8.11512778  6.26038596  6.9350914
  4.43174992  7.15405678 11.08172742  5.02215851  6.5311071   5.39882307]
[11.42689122 10.70691862  9.70303346  9.57264593  8.15771069  7.12924317
  7.69925375  6.71084551  8.06512366  8.18684305  6.28110433  7.11569199
  4.41562925  7.25275918 11.24977112  5.03317877  6.63427311  5.37861011]
[11.44198152 10.76233806  9.76733477  9.66842621  8.20575211  7.21955852
  7.80206696  6.7300522   8.32031544  8.24954965  6.28516053  7.17605457
  4.42868238  7.27063605 11.29908088  5.04580633  6.67683844  5.34298943]
[11.64990283 10.7545845   9.60778595  9.3836841   8.19774247  7.00743257
  7.26735485  6.71498546  7.79530517  8.04172301  6.30299217  7.13146158
  4.39397794  7.23270737 11.27155765  4.96096075  6.62700545  5.38117424]
[11.23140811 10.55442176  9.5085923   9.38030433  7.94224063  6.93753707
  7.46036711  6.66940441  7.78547248  7.92432726

 4.08414041 7.08669325 9.48419577 4.85375639 5.81878441 4.63717575]
[9.95039611 9.44179426 7.92182419 8.35520377 7.69303782 6.18611202
 6.57453983 5.75217044 6.70588271 6.23325291 5.56275969 5.87754971
 4.05520755 7.0601719  9.56242576 4.75775662 5.69765869 4.60762662]
[9.90798848 9.33923103 7.97833311 8.64561994 7.66020286 6.41601243
 6.91182243 5.94895375 7.0000935  6.71071443 5.55567873 6.07795248
 4.10780007 7.21097991 9.6488454  4.80782495 6.03431765 4.66753213]
[9.66064543 9.12774361 7.73908446 8.64277809 7.63406061 6.42463617
 6.90612337 5.94740654 7.07748923 6.75022007 5.50308892 5.99552412
 4.08250737 7.29471857 9.56841784 4.77429298 6.04039315 4.57257492]
[9.75419109 9.26716488 7.94528964 8.37134808 7.62478963 6.40920468
 7.01153231 5.95143067 6.88316845 6.76677616 5.60448312 5.96351526
 4.15539467 7.00940506 9.49749148 4.91235487 5.72126699 4.75978186]
[9.90071307 9.10653799 7.76994202 8.4365536  7.47252798 6.36591918
 6.71005982 5.79143093 6.50432661 6.5230559  5.53859355 5

 4.06295405 7.25896166 8.98069888 4.55597381 5.62871666 4.61001605]
[9.69000777 8.81470233 7.27790428 8.23276397 7.82860788 6.58362511
 6.88780026 5.92830604 6.89632783 6.32515368 5.31237404 6.26252267
 4.0858262  7.28699607 8.88649359 4.53824466 5.74113319 4.65763142]
[9.80483076 8.87934313 7.27712358 8.32790767 7.74371796 6.63648978
 6.83677922 5.88319972 7.03739116 6.31142214 5.36609133 6.31652149
 4.07894724 7.30809295 9.07521946 4.52577074 5.71295589 4.63654086]
[9.63895887 8.87930945 7.24984688 8.1370462  7.81246908 6.53933395
 6.79517752 5.8390685  6.84161759 6.33471328 5.37708191 6.26666885
 4.07891135 7.2243794  9.00630247 4.57629305 5.56187217 4.59410624]
[9.68252162 8.87760422 7.31356997 8.27543119 7.81509293 6.60642654
 6.75014614 5.93337242 6.9621047  6.35226926 5.35837845 6.17944457
 4.07615514 7.29370775 9.04273609 4.53271509 5.74012686 4.70239647]
[9.52316842 8.77314973 7.21893817 8.25795264 7.74498434 6.5039233
 6.82985668 5.85639346 6.99828078 6.37135483 5.31255626 6.

 4.08992085 7.30611545 9.00387206 4.58859133 5.66110953 4.75290501]
[9.7000862  8.98459524 7.38051119 8.26944745 8.04457432 6.62339102
 6.82988529 5.86810771 7.12177264 6.38233666 5.36787827 6.30676331
 4.08969473 7.32585929 9.03335888 4.5573059  5.68172942 4.75463426]
[9.63375326 8.95949186 7.37823423 8.26888251 8.09331144 6.69510457
 6.8929481  5.87576088 7.15292612 6.45813505 5.38997607 6.28678411
 4.1027608  7.33439683 8.98634057 4.57492938 5.7005189  4.77748717]
[9.67917029 9.01126304 7.38268383 8.28474422 8.10795389 6.67315491
 6.86448464 5.84989809 7.24298462 6.38963466 5.43052418 6.26024784
 4.09645181 7.33612587 9.05696521 4.57487608 5.65659726 4.75603972]
[9.62896707 8.91381949 7.32707466 8.24841324 8.05687641 6.65305256
 6.86095449 5.87341117 7.19212253 6.36536575 5.36792753 6.22434909
 4.09316315 7.3249718  8.9485174  4.54814267 5.67207152 4.76582257]
[9.67576765 8.96438571 7.33739289 8.24897253 8.13286529 6.62860318
 6.85253643 5.84942358 7.170494   6.33694385 5.37964862 6

In [29]:
data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Radiant Advantage":np.exp(res.x[-1])}
data
Teamhg = pd.DataFrame(data)
Teamhg.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg

Teams     Ranks  Radiant Advantage
0                    OG  1.506624           2.497178
1           Team Liquid  1.432192           2.497178
14        Natus Vincere  1.426334           2.497178
3           Team Secret  1.362046           2.497178
4           Vici Gaming  1.359377           2.497178
2               PSG.LGD  1.284708           2.497178
13              Mineski  1.279778           2.497178
8                Newbee  1.273076           2.497178
6   Royal Never Give Up  1.239052           2.497178
5         Evil Geniuses  1.214277           2.497178
9          TNC Predator  1.200856           2.497178
11               Fnatic  1.185388           2.497178
7       Infamous Gaming  1.152014           2.497178
16          KEEN GAMING  1.141608           2.497178
10           Virtus.pro  1.115553           2.497178
17    Ninjas in Pyjamas  1.071906           2.497178
15   Chaos Esports Club  1.054776           2.497178
12             Alliance  1.022962           2.497178

In [30]:
np.sum(aij,axis=1)

array([ 8., 13.,  3.,  8.,  7.,  4.,  5.,  2.,  7.,  5.,  2.,  5.,  4.,
        5.,  5.,  1.,  3.,  2.])

In [31]:
Teamlist

['OG',
 'Team Liquid',
 'PSG.LGD',
 'Team Secret',
 'Vici Gaming',
 'Evil Geniuses',
 'Royal Never Give Up',
 'Infamous Gaming',
 'Newbee',
 'TNC Predator',
 'Virtus.pro',
 'Fnatic',
 'Alliance',
 'Mineski',
 'Natus Vincere',
 'Chaos Esports Club',
 'KEEN GAMING',
 'Ninjas in Pyjamas']

In [32]:
np.sum(bij,axis=1)

array([1., 9., 3., 6., 5., 2., 8., 5., 7., 8., 7., 8., 3., 5., 5., 5., 8.,
       9.])

Lets add some extra data to represent whether a team's composition has won

In [83]:
Teamskill1 = np.zeros(m)
Teamskill2 = np.zeros(m)

index = 0
for i in heroes1new:
    for j in i:
        Teamskill1[index] += test4["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in heroes2new:
    for j in i:
        Teamskill2[index] += test4["Ranks"][hdict[j]][0]
    index += 1

In [84]:
Teamwin1 = np.zeros(m)
for i in range(m):
    prob = Teamskill1[i]/(Teamskill1[i]+Teamskill2[i])
    if prob >= 0.5:
        Teamwin1[i] = 1

In [85]:
Teamwin1

array([1., 1., 1., 1., 0., 1., 1., 0., 1., 1., 0., 0., 1., 0., 1., 1., 1.,
       0., 1., 0., 0., 1., 1., 0., 1., 0., 1., 0., 1., 0., 0., 0., 0., 1.,
       1., 0., 1., 0., 1., 0., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1., 1.,
       1., 0., 0., 0., 1., 1., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1., 0.,
       1., 0., 0., 0., 0., 0., 1., 0., 1., 0., 0., 1., 0., 0., 0., 1., 0.,
       0., 0., 1., 1., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0.,
       0., 1., 0., 0., 1., 1., 0., 1., 1., 1., 0., 1., 0., 1., 1., 0., 0.,
       0., 0., 0., 0., 1., 1., 0., 0., 1., 1., 1., 0., 1., 0., 1., 0., 0.,
       0., 1., 1., 0., 0., 1., 1., 1., 0., 0., 1., 0., 0., 1., 1., 1., 1.,
       1., 1., 0., 1., 0., 0., 0., 1., 1., 0., 1., 1., 0., 0., 1., 0., 0.,
       0., 1., 1., 0., 1., 1., 0., 1., 0., 1., 0., 0., 1., 0., 1., 0., 1.,
       1., 0., 1., 0., 1., 1.])

In [86]:
games['Team Winner'] = Teamwin1

In [113]:
Teamskill3 = np.zeros(m)
Teamskill4 = np.zeros(m)

index = 0
m = len(games["Winner"])
for i in heroes1new:
    for j in i:
            Teamskill3[index] += Heroskills2["Ranks"][hdict[j]]
    index += 1

index = 0
for i in heroes2new:
    for j in i:
            Teamskill4[index] += Heroskills2["Ranks"][hdict[j]]            
    index += 1

Teamskill3

array([0.05304566, 0.08208173, 0.0419388 , 0.04674281, 0.03885561,
       0.05019792, 0.0711452 , 0.04109556, 0.04915106, 0.05592003,
       0.05482503, 0.05471551, 0.03524727, 0.05906675, 0.03801935,
       0.08367657, 0.05542384, 0.03020628, 0.0503831 , 0.04956281,
       0.05343653, 0.06987014, 0.04835914, 0.05567361, 0.0364725 ,
       0.05667536, 0.06115766, 0.03121343, 0.05634916, 0.05671534,
       0.06714711, 0.05684814, 0.06388068, 0.06219287, 0.06103658,
       0.06759205, 0.0789511 , 0.06909837, 0.08596377, 0.04008453,
       0.03695874, 0.04295332, 0.04152689, 0.06187216, 0.07730583,
       0.06797797, 0.0471235 , 0.05128018, 0.08418205, 0.0350641 ,
       0.05141663, 0.05870093, 0.06788029, 0.05605384, 0.07349059,
       0.06755227, 0.07334225, 0.0688061 , 0.03565452, 0.04725747,
       0.04507297, 0.07014322, 0.04665595, 0.0463109 , 0.04392802,
       0.03746759, 0.04933698, 0.03632554, 0.02118794, 0.05657473,
       0.06942749, 0.0586125 , 0.06770914, 0.05933572, 0.05221

In [115]:
Teamwin2 = np.zeros(m)
for i in range(m):
    if Teamskill3[i] > Teamskill4[i]:
        Teamwin2[i] = 1

Teamwin2

array([1., 1., 0., 0., 1., 1., 1., 1., 1., 0., 1., 1., 0., 1., 0., 1., 1.,
       0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1., 1., 1., 1.,
       0., 0., 1., 1., 1., 1., 0., 0., 0., 1., 1., 1., 0., 0., 1., 0., 0.,
       1., 1., 1., 1., 1., 1., 1., 0., 1., 1., 1., 1., 0., 0., 0., 0., 0.,
       0., 0., 1., 1., 0., 0., 1., 1., 0., 1., 0., 1., 0., 1., 0., 0., 0.,
       1., 0., 1., 1., 1., 1., 0., 1., 1., 1., 1., 0., 0., 0., 1., 0., 0.,
       0., 1., 1., 0., 1., 0., 1., 0., 0., 1., 1., 0., 1., 0., 1., 1., 0.,
       0., 1., 1., 0., 0., 1., 1., 0., 1., 0., 1., 1., 0., 0., 0., 0., 1.,
       1., 0., 0., 1., 1., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1.,
       0., 1., 0., 0., 1., 0., 0., 1., 0., 0., 1., 1., 0., 0., 0., 0., 0.,
       0., 0., 1., 0., 1., 1., 0., 0., 0., 0., 1., 0., 1., 0., 0., 0., 0.,
       1., 0., 0., 0., 1., 0.])

In [120]:
games['Team Winner 2'] = Teamwin2

In [121]:
k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Team Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(games["Team Winner"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 1":np.exp(res.x[-1])}

Teamhg2 = pd.DataFrame(data)
Teamhg2.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg2

k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Team Winner 2"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(games["Team Winner 2"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 2":np.exp(res.x[-1])}

Teamhg3 = pd.DataFrame(data)
Teamhg3.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg3


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log


[34.20426344 18.58546601 15.59810715 13.92794587 20.93028305 20.82685522
 28.10459393 20.53853998 24.26122266 22.21634423 26.05369435 34.68288461
  9.43904461 13.04654173 17.95333233 10.57293746 24.7434024  22.41575561]
[34.4656223  18.66649828 15.68636589 13.81281589 20.88245736 20.89166256
 27.93933796 20.40854848 24.50198787 22.26122799 26.23886312 34.80766425
  9.41996105 13.08173786 18.05688018 10.61047966 24.63199173 22.27803862]
[34.25770706 18.63957956 15.66292009 13.88440383 20.81285184 20.41039581
 28.08297777 21.05018495 24.39888248 22.53108163 26.24182813 34.5667651
  9.44007665 13.06957323 18.02235993 10.82346045 24.86948198 22.25873333]
[34.76782245 18.90413685 15.92201904 13.92955419 20.79868942 20.82571699
 28.13796032 20.57126745 24.388844   22.63097171 26.50992373 35.52492796
  9.34297598 13.15607266 18.19029526  9.60539189 24.81682828 22.11574742]
[34.90420544 18.84831601 15.86956856 13.89920444 20.74919323 20.71069732
 28.00161428 20.43573279 24.2686286  22.3022108 

[30.79802558 25.64015114 18.66398956 13.50533956 19.26860108 25.9364394
 18.1252025  17.24796835 26.74009131 16.42440331 19.02787796 31.34257615
  7.28757468 15.15478639 23.27560908  7.92727707 14.02030956 10.14104891]
[30.29502895 25.7204     18.71658381 13.64202206 20.8990449  25.34418636
 17.0178897  18.00501678 27.20216372 19.00677702 18.33614137 30.75585651
  7.21244827 15.33593773 24.16291758  8.59710916 11.9749724   9.74454675]
[30.13316127 25.86726409 18.72251184 13.80625741 21.82632749 24.45160728
 16.55890616 18.18295785 27.11123334 20.63656548 18.52241403 31.52329755
  7.16501994 15.43262022 24.91094073  7.91371092 10.79247647  8.90168311]
[28.83362658 25.68053271 18.5670154  13.24579556 21.32167778 27.06695309
 15.79594409 17.8119986  27.60905565 16.76222141 16.75542688 26.70149002
  7.08656935 15.35624069 23.95049657 10.32309567 10.78095583 10.31802367]
[29.84380672 26.23747654 18.77303206 13.62453529 20.464615   26.35423855
 16.18352301 16.83906066 27.34163255 17.76654323

  6.84130601 14.12409881 22.06733906  8.5407713  11.79479325 10.54234636]
[23.57144223 25.57376353 16.582218   14.25325438 21.54268934 16.05545564
 15.6868237  12.17491228 24.0687614  15.8849229  22.56488379 21.4427791
  6.82216143 14.16857907 22.51087876  7.31030834 12.68396111  9.77721883]
[20.64500985 24.85907168 16.4342815  14.31639529 22.04508405 14.52418155
 16.22142086 11.60785266 23.41378494 17.97425711 23.45155566 20.43469625
  6.81763989 13.97992051 21.97852213  8.175572   13.36363593  9.51171928]
[20.9832543  26.16159848 16.73338279 14.50405655 22.46148687 16.2696381
 13.55109192 11.62197085 24.34835707 18.19712825 20.73518576 21.92317756
  6.59766857 14.36791935 23.27371924  7.17030111  9.94601322  8.42610164]
[23.51025927 26.1857299  17.13344574 14.25879752 20.42857803 16.1334109
 15.08389053 12.81538204 24.44061531 15.78000934 20.9003773  23.70943947
  6.8020278  14.37881113 22.4417412   8.10707625 13.27068943  9.12512178]
[24.96858265 26.87163203 17.54810568 14.2671016  

...

[11.38459369 13.21814837 10.2020714   8.7850693   8.11394568  6.96502395
  7.50216771  6.77384402  8.0050289   7.7300608   6.71888844  7.56529978
  4.61413914  7.93996446  6.68703085  5.18495732  6.14212691  5.4882155 ]
[11.41645384 13.37332244 10.20675939  8.89822684  8.09025032  6.90761682
  7.58555447  6.7345287   7.92036333  7.62496513  6.71104407  7.52687143
  4.59532484  7.95093646  6.63066292  5.13157774  6.17495403  5.43555212]
[11.58608542 13.35926774 10.22788642  8.88591795  8.20076639  7.06115395
  7.65745769  6.77191816  7.956524    7.7609353   6.70250653  7.62678935
  4.62222931  7.978117    6.76443515  5.17839612  6.17520703  5.45187101]
[11.45870362 13.33381035 10.12839387  8.93310964  8.09772615  7.0285551
  7.63789481  6.76957312  8.01278828  7.71411422  6.73819871  7.65755585
  4.63174919  7.93528751  6.76510252  5.11962178  6.19908054  5.52427107]
[11.45527218 13.34247676 10.255435    8.84570245  8.20865642  6.92414476
  7.58533014  6.75202156  7.9379189   7.7548003 

  4.58783498  7.92368234  6.64275502  5.08540024  6.14732797  5.44068807]
[11.80841573 13.48330347 10.24075813  9.03560295  7.97022446  7.0521542
  7.50661446  6.7355377   7.95238013  7.93604186  6.74843335  7.45152918
  4.60753282  7.96752714  6.64823417  5.09832211  6.22860838  5.46716308]
[11.59231725 13.37305254 10.12667384  9.00231411  7.94200505  7.07091278
  7.44021233  6.68087362  7.82458158  7.887987    6.65664426  7.3915133
  4.60033767  7.90840249  6.66337478  5.08492324  6.17603162  5.48154369]
[11.53816119 13.43295674 10.18181753  8.99670026  7.90074179  7.02509289
  7.45489863  6.61524758  7.82844093  7.85561589  6.63432418  7.45149581
  4.57929221  7.92815612  6.5802657   5.08947153  6.18856954  5.45187458]
[11.73696456 13.42677532 10.14634945  9.0261259   7.92456616  7.03372818
  7.49821339  6.64505011  7.95780944  7.95731615  6.7464694   7.43517256
  4.61552147  7.91845648  6.64680457  5.11746993  6.22586161  5.52078945]
[11.66368265 13.41829084 10.14758892  9.00758646

  4.57687266  7.79587428  6.44794797  5.04074962  6.12165623  5.34933589]
[11.57731579 13.21783239  9.99418072  8.89170046  7.74552835  6.94155926
  7.41793228  6.61673701  7.7722061   7.95229597  6.53129585  7.2846658
  4.57648524  7.80906027  6.44143606  5.03566486  6.13417265  5.3645294 ]
[11.55287385 13.1470223   9.99918354  8.81604819  7.74096561  6.98369754
  7.43527408  6.621692    7.75558559  7.95635853  6.52063847  7.3682221
  4.57510144  7.80508455  6.4456295   5.04554607  6.12405375  5.35103172]
[11.57342677 13.15185872 10.02784885  8.82712524  7.77408797  6.99478436
  7.43046158  6.65281468  7.77430418  7.96267374  6.52541142  7.32094312
  4.57974302  7.8215589   6.46833252  5.06556966  6.1429085   5.34676502]
[11.5601376  13.17424262  9.99627301  8.85297063  7.725625    6.99881594
  7.41210065  6.61936796  7.74518851  7.95662884  6.55552636  7.35584294
  4.57664553  7.80370039  6.45520897  5.05069608  6.13229047  5.35758803]
[11.63006731 13.20460701 10.04395265  8.86152355

  4.55877977  7.78601973  6.36257561  5.04484292  6.08330339  5.32101796]
[11.487537   13.26474211 10.01785228  8.91872132  7.79354149  6.99198678
  7.42570136  6.6220981   7.79590769  8.00357543  6.5538366   7.36798804
  4.57605884  7.81397336  6.40469568  5.04284372  6.11036205  5.3358236 ]
[11.35579851 13.18340724  9.97136139  8.8672616   7.68930123  6.96866678
  7.358107    6.5676506   7.73338651  7.9631936   6.48787905  7.30395197
  4.5558371   7.77588629  6.34921077  5.01865567  6.0722501   5.30978775]
[11.43494233 13.16107616  9.98472854  8.84389659  7.73543801  7.02132686
  7.3897958   6.61236567  7.74692505  8.01300582  6.522406    7.37720483
  4.57072305  7.78648422  6.38213696  5.04745243  6.08832583  5.34246366]
[11.39576033 13.13244126  9.94330674  8.82867006  7.68523305  6.93970357
  7.32024256  6.58773549  7.70082138  7.9747951   6.55441077  7.31548112
  4.56227601  7.74825087  6.36086264  5.03399479  6.06826849  5.29799126]
[11.41365379 13.20881539  9.989818    8.884952

Teams     Ranks  Draft Advantage 2
1           Team Liquid  1.875062           2.414872
0                    OG  1.651369           2.414872
2               PSG.LGD  1.503803           2.414872
3           Team Secret  1.381570           2.414872
9          TNC Predator  1.305646           2.414872
4           Vici Gaming  1.285252           2.414872
13              Mineski  1.283747           2.414872
8                Newbee  1.276599           2.414872
6   Royal Never Give Up  1.242112           2.414872
11               Fnatic  1.233961           2.414872
5         Evil Geniuses  1.216781           2.414872
7       Infamous Gaming  1.184003           2.414872
10           Virtus.pro  1.173352           2.414872
14        Natus Vincere  1.161912           2.414872
16          KEEN GAMING  1.136057           2.414872
17    Ninjas in Pyjamas  1.079258           2.414872
15   Chaos Esports Club  1.056563           2.414872
12             Alliance  1.022005           2.414872

In [122]:
Teamhg3

Teams     Ranks  Draft Advantage 2
1           Team Liquid  1.875062           2.414872
0                    OG  1.651369           2.414872
2               PSG.LGD  1.503803           2.414872
3           Team Secret  1.381570           2.414872
9          TNC Predator  1.305646           2.414872
4           Vici Gaming  1.285252           2.414872
13              Mineski  1.283747           2.414872
8                Newbee  1.276599           2.414872
6   Royal Never Give Up  1.242112           2.414872
11               Fnatic  1.233961           2.414872
5         Evil Geniuses  1.216781           2.414872
7       Infamous Gaming  1.184003           2.414872
10           Virtus.pro  1.173352           2.414872
14        Natus Vincere  1.161912           2.414872
16          KEEN GAMING  1.136057           2.414872
17    Ninjas in Pyjamas  1.079258           2.414872
15   Chaos Esports Club  1.056563           2.414872
12             Alliance  1.022005           2.414872

In [123]:
Teamhg3

Teams     Ranks  Draft Advantage 2
1           Team Liquid  1.875062           2.414872
0                    OG  1.651369           2.414872
2               PSG.LGD  1.503803           2.414872
3           Team Secret  1.381570           2.414872
9          TNC Predator  1.305646           2.414872
4           Vici Gaming  1.285252           2.414872
13              Mineski  1.283747           2.414872
8                Newbee  1.276599           2.414872
6   Royal Never Give Up  1.242112           2.414872
11               Fnatic  1.233961           2.414872
5         Evil Geniuses  1.216781           2.414872
7       Infamous Gaming  1.184003           2.414872
10           Virtus.pro  1.173352           2.414872
14        Natus Vincere  1.161912           2.414872
16          KEEN GAMING  1.136057           2.414872
17    Ninjas in Pyjamas  1.079258           2.414872
15   Chaos Esports Club  1.056563           2.414872
12             Alliance  1.022005           2.414872

In [43]:
import random
Train = random.sample(range(193), 97)
Train
total = range(193)
Test = []
for i in total:
    if i not in Train:
        Test.append(i)
Test

trainRadiant = games["Radiant"][97:]
trainDire = games["Dire"][97:]
trainWinner = games["Winner"][97:]

trainGames = pd.DataFrame(data = {'Radiant':trainRadiant,'Dire':trainDire,'Winner':trainWinner})
trainGames

testRadiant = games["Radiant"][0:96]
testDire = games["Dire"][0:96]
testWinner = games["Winner"][0:96]

testGames = pd.DataFrame(data = {'Radiant':testRadiant,'Dire':testDire,'Winner':testWinner})
testGames

Radiant                 Dire  Winner
0                    OG          Team Liquid     1.0
1           Team Liquid                   OG     0.0
2           Team Liquid                   OG     0.0
3           Team Liquid                   OG     1.0
4               PSG.LGD          Team Liquid     0.0
5           Team Liquid              PSG.LGD     1.0
6           Team Liquid              PSG.LGD     0.0
7           Team Secret          Team Liquid     0.0
8           Team Liquid          Team Secret     1.0
9                    OG              PSG.LGD     1.0
10              PSG.LGD                   OG     0.0
11                   OG              PSG.LGD     0.0
12          Team Secret          Vici Gaming     1.0
13          Vici Gaming          Team Secret     0.0
14          Team Liquid        Evil Geniuses     1.0
15          Team Liquid        Evil Geniuses     1.0
16          Team Secret      Infamous Gaming     1.0
17      Infamous Gaming          Team Secret     0.0
18          Team Liquid  Royal Never Give Up     1.0
19  Royal Never Give Up          Team Liquid     0.0
20                   OG        Evil Geniuses     1.0
21                   OG        Evil Geniuses     1.0
22        Evil Geniuses                   OG     1.0
23          Vici Gaming              PSG.LGD     0.0
24          Vici Gaming              PSG.LGD     0.0
25              Mineski          Team Secret     0.0
26              Mineski          Team Secret     1.0
27              Mineski          Team Secret     0.0
28               Newbee      Infamous Gaming     0.0
29      Infamous Gaming               Newbee     0.0
..                  ...                  ...     ...
66          Vici Gaming        Natus Vincere     1.0
67        Evil Geniuses           Virtus.pro     0.0
68    Ninjas in Pyjamas      Infamous Gaming     1.0
69  Royal Never Give Up               Fnatic     0.0
70           Virtus.pro        Evil Geniuses     0.0
71        Natus Vincere          Vici Gaming     0.0
72      Infamous Gaming    Ninjas in Pyjamas     1.0
73          Team Secret              PSG.LGD     0.0
74          Team Liquid          KEEN GAMING     1.0
75          Team Secret              PSG.LGD     0.0
76               Newbee   Chaos Esports Club     1.0
77              Mineski             Alliance     0.0
78               Fnatic                   OG     0.0
79               Newbee   Chaos Esports Club     1.0
80          KEEN GAMING          Team Liquid     0.0
81             Alliance              Mineski     0.0
82               Fnatic                   OG     0.0
83  Royal Never Give Up        Natus Vincere     1.0
84    Ninjas in Pyjamas          Vici Gaming     1.0
85      Infamous Gaming           Virtus.pro     0.0
86        Natus Vincere  Royal Never Give Up     0.0
87          Vici Gaming    Ninjas in Pyjamas     1.0
88           Virtus.pro      Infamous Gaming     1.0
89         TNC Predator   Chaos Esports Club     0.0
90             Alliance          Team Liquid     1.0
91          KEEN GAMING               Newbee     1.0
92              Mineski          Team Secret     1.0
93          Team Liquid             Alliance     1.0
94         TNC Predator   Chaos Esports Club     1.0
95          Team Secret              Mineski     1.0

[96 rows x 3 columns]

In [44]:
trainTeamsX = designMatrix(trainGames, index_dict)
trainTeams = BTfit(trainTeamsX, trainGames["Winner"], Teamlist,1)

In [45]:
trainTeams

Teams                   Ranks
0                    OG     [2.840385798173282]
1           Team Liquid   [-0.3046810887345014]
2               PSG.LGD    [1.9901626442372549]
3           Team Secret     [2.892053260280484]
4           Vici Gaming    [1.2795604021292535]
5         Evil Geniuses    [1.0521698545560705]
6   Royal Never Give Up    [-0.975257687074863]
7       Infamous Gaming    [1.3314696739609841]
8                Newbee    [1.2861607827156005]
9          TNC Predator    [1.1424430752350416]
10           Virtus.pro   [-0.9771617297025272]
11               Fnatic    [0.7043566292250386]
12             Alliance    [0.7448658902417994]
13              Mineski    [0.2033268315603538]
14        Natus Vincere    [1.0352982060976934]
15   Chaos Esports Club    [-1.879336589675658]
16          KEEN GAMING  [-0.05767535237306112]
17    Ninjas in Pyjamas    [-2.259397093942969]

In [46]:
wins = 0
for i in range(len(testGames["Radiant"])):
    li = trainTeams["Ranks"][index_dict[testGames["Radiant"][i]]][0]
    lj = trainTeams["Ranks"][index_dict[testGames["Dire"][i]]][0]
    result = testGames["Winner"][i]
    pi = li/(li + lj)
    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy1 = wins/len(testGames["Radiant"])
test_accuracy1

49


0.5104166666666666

In [47]:
heroes1 = []
heroes2 = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        heroes1.append(Stats[i][2])
        heroes2.append(Stats[i][5])
        i += 1   
heroes1new = []
heroes2new = []
for i in heroes1:
    heroes1new.append(i.split("  "))

for i in heroes2:
    heroes2new.append(i.split("  "))

    
trainHeroes1 = heroes1new[97:]
trainHeroes2 = heroes2new[97:]
testHeroes1 = heroes1new[0:96]
testHeroes2 = heroes2new[0:96]

Matchups1 = []
binWins2 = []
for i in trainHeroes1:
    for j in i:
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)


Matchups2 = []
for i in trainHeroes2:
    for j in range(5):
        Matchups2.append(i[0])
        Matchups2.append(i[1])
        Matchups2.append(i[2])
        Matchups2.append(i[3])
        Matchups2.append(i[4])

    
for i in binWins[97:]:
    for j in range(25):
        binWins2.append(i)

d = {'Radiant':Matchups1, 'Dire':Matchups2, 'Winner':binWins2}
trainHeroGames = pd.DataFrame(data = d)


In [132]:
trainHeroes1X = designMatrix(trainHeroGames, hdict)
trainHeroesSkill1 = BTfit(trainHeroes1X, binWins2, heroes,1)
trainHeroesSkill1

Teams                    Ranks
0                  Io     [1.6160153437448854]
1                Tiny     [0.9179254604717398]
2             Abaddon     [0.8164228749439403]
3           Timbersaw   [0.030441769714830536]
4          Gyrocopter     [1.3745739118103146]
5              Rubick     [0.5472019006137392]
6          Tidehunter     [1.4410780892608135]
7           Ogre Magi      [0.905210958388527]
8    Templar Assassin     [1.5285340814925927]
9          Juggernaut    [0.10049623937447479]
10      Shadow Shaman     [1.3559923270366776]
11        Lifestealer     [1.0186035210436881]
12             Enigma    [0.23735979654690884]
13               Chen     [1.7183448537255233]
14              Meepo    [0.12010477769759088]
15        Elder Titan      [1.013002480969177]
16      Faceless Void      [0.626466787939354]
17       Shadow Fiend     [0.8354883308623896]
18          Dark Seer    [0.05195754510253359]
19               Sven     [0.8106373462837984]
20             Mirana     [1.1369130415961701]
21             Tinker     [0.8183500113899145]
22       Shadow Demon     [1.2172595675675308]
23             Magnus     [1.0715908638742908]
24        Wraith King     [1.0784600052190556]
25        Bristleback      [2.033864628492551]
26       Earth Spirit     [1.7923518140375156]
27            Leshrac     [1.0480740738244758]
28          Alchemist     [1.1003820909325563]
29   Legion Commander     [1.3248775475582513]
..                ...                      ...
85        Drow Ranger    [-1.6487289833204377]
86      Skywrath Mage      [2.316772096188394]
87        Dark Willow     [1.4456141183798619]
88         Naga Siren      [1.574793741182475]
89            Undying     [0.6473616833221111]
90            Spectre       [1.22968689105579]
91              Pudge     [0.1845432458469322]
92             Clinkz    [0.25241685704652483]
93        Bloodseeker   [-0.10249506090331921]
94       Chaos Knight    [0.44229369290628395]
95              Viper     [0.6697515909881231]
96               Bane  [-0.005800880077114239]
97            Slardar      [1.232891376941071]
98             Huskar     [-0.738974405153235]
99      Troll Warlord   [-0.25177066814963744]
100        Lone Druid    [-2.5166702242983927]
101   Vengeful Spirit    [-2.3807514039938074]
102  Treant Protector     [2.7258190425631925]
103            Dazzle     [0.1565840072554196]
104         Disruptor     [-2.170577737355993]
105           Phoenix   [-0.48130733297686185]
106              Tusk     [0.9497064796778601]
107              Luna    [-1.1205027613987215]
108              Doom    [-1.0684425780217857]
109             Lycan    [-1.3344602338512248]
110    Spirit Breaker    [-0.9501670015014304]
111     Night Stalker    [0.46466286286095304]
112     Bounty Hunter   [0.029759316991142204]
113        Venomancer    [-1.7358577840627054]
114      Ember Spirit     [-0.903718294164281]

[115 rows x 2 columns]

In [133]:
testTeamskill1 = np.zeros(96)
testTeamskill2 = np.zeros(96)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
testTeamskill1
testTeamskill2

array([ 7.62955582,  3.84568532,  4.55986366,  4.91328548,  5.51138742,
        2.75967284,  5.19053867,  4.08506616,  3.82358569,  5.02927911,
        2.83844295,  4.54725717,  5.13011768,  5.57686712,  4.97658213,
        5.62804049,  3.76433695,  5.34887017,  4.14163814,  5.38618006,
        4.76679859,  5.18085605,  7.255769  ,  5.23206913,  4.03363465,
        2.71756939,  4.87686127,  2.34422867,  6.09422109,  4.03853128,
        6.64372392,  4.93810914,  5.38589284,  5.00401346,  4.75809071,
        5.73866386,  4.96201837,  6.36980915,  7.16901939,  4.82305711,
        4.33498296,  7.16795441,  3.79828941,  5.91637661,  5.64498498,
        5.69355437,  4.78608329,  6.46168118,  5.17429339,  4.06981649,
        4.43706656,  6.44692323,  3.4284153 ,  5.1658549 ,  5.32453267,
        5.2339009 ,  3.06727747,  5.13827103,  2.77969423,  2.83498808,
        2.52571377,  5.49879841,  6.77067562,  3.71089817,  5.45447807,
        5.0111019 ,  2.49538894,  4.65756724,  3.17541107,  5.60

In [134]:
testTeamwin1 = 0
for i in range(96):
    prob = testTeamskill1[i]/(testTeamskill1[i]+testTeamskill2[i])
    result = testGames["Winner"][i]
    if prob < 0.5 and result ==0:
        testTeamwin1 += 1
    if prob >= 0.5 and result ==1:
        testTeamwin1 += 1
test_accuracy2 = testTeamwin1/len(testGames["Radiant"])
test_accuracy2


0.5

In [135]:
k = len(hdict.keys())
r = []

r = np.array(trainWinner)
m = len(r)



Ip = np.zeros((m,k))
I = np.zeros((m,k))
l = 0
for i in trainHeroes1:
    for j in i:
        if trainGames["Winner"][97+l] == 1:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l+=1

l = 0
for i in trainHeroes2:
    for j in i:
        if trainGames["Winner"][97+l] == 0:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l += 1  


trainHeroesSkill2 = BTfit2(I,Ip,r,k,10,heroes)

[7.29811423e-01 4.14351017e-01 1.50988448e-02 9.08975157e-01
 7.89378718e-01 1.65199169e-01 3.12785961e-01 6.10945306e-01
 3.64490287e-01 1.56038589e-01 1.77303813e-01 8.67889671e-01
 2.90094668e-01 5.85179621e-01 4.53994876e-01 4.11178132e-01
 8.82634445e-01 6.92708015e-01 2.79273355e-01 6.44402312e-02
 1.98623614e-01 9.31682745e-01 8.54413568e-01 9.54734735e-01
 5.22533482e-02 5.79471681e-01 4.80496267e-01 2.17089790e-02
 3.73620464e-01 4.14091801e-01 6.03907234e-01 6.71748727e-01
 8.38865700e-01 7.79526208e-01 4.00701044e-01 7.94529231e-01
 8.93124310e-01 2.62489691e-01 9.89197007e-01 8.53307099e-01
 7.31477156e-01 3.55565625e-01 8.83289491e-01 8.67959091e-01
 9.55766446e-01 1.07256520e-04 1.65410419e-02 3.14070057e-01
 9.95316175e-01 1.48844223e-01 1.67377119e-01 7.58572037e-01
 6.95296662e-02 7.05473439e-01 4.69165282e-01 1.01882161e-02
 7.74823863e-01 7.94201008e-01 1.49569452e-01 2.37036318e-02
 7.62063771e-01 2.23670180e-01 2.62174398e-01 4.56869503e-01
 2.49926919e-01 5.682835

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:62: RuntimeWarning: invalid value encountered in double_scalars


In [136]:
testTeamskill3 = np.zeros(96)
testTeamskill4 = np.zeros(96)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
testTeamskill3
testTeamskill4

testTeamwin2 = 0
for i in range(96):
    prob = testTeamskill3[i]/(testTeamskill3[i]+testTeamskill4[i])
    result = testGames["Winner"][i]
    if prob < 0.5 and result ==0:
        testTeamwin2 += 1
    if prob >= 0.5 and result ==1:
        testTeamwin2 += 1
test_accuracy3 = testTeamwin2/len(testGames["Radiant"])
test_accuracy3

0.4270833333333333

In [163]:
wincounts = np.zeros(len(Teamlist))
index = 97
for i in trainGames["Radiant"]:
    if trainGames["Winner"][index] == 1:
        wincounts[index_dict[i]] += 1
    index+=1

index = 97
for i in trainGames["Dire"]:
    if trainGames["Winner"][index] == 0:
        wincounts[index_dict[i]] += 1
    index+=1
    
wincounts

array([11.,  3., 10.,  9.,  7.,  6.,  3.,  5.,  5.,  6.,  3.,  5.,  5.,
        5.,  7.,  1.,  4.,  1.])

In [164]:
trainTeamskill1 = np.zeros(m)
trainTeamskill2 = np.zeros(m)

index = 0
for i in trainHeroes1:
    for j in i:
        trainTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in trainHeroes2:
    for j in i:
        trainTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1

trainTeamskill3 = np.zeros(m)
trainTeamskill4 = np.zeros(m)

index = 0
for i in trainHeroes1:
    for j in i:
        trainTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in trainHeroes2:
    for j in i:
        trainTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    
trainTeamwin1 = np.zeros(m)
for i in range(m):
    prob = trainTeamskill1[i]/(trainTeamskill1[i] + trainTeamskill2[i])
    if prob >= 0.5:
        trainTeamwin1[i] = 1    

trainTeamwin2 = np.zeros(m)
for i in range(m):
    if trainTeamskill3[i]>(trainTeamskill4[i]):
        trainTeamwin2[i] = 1

trainGames["Team Winner"] =trainTeamwin1
trainGames["Team Winner 2"] = trainTeamwin2

k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 97

for i in trainGames["Radiant"]:
    j = trainGames["Dire"][l]
    if trainGames["Team Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(trainGames["Team Winner"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 1":np.exp(res.x[-1])}


Teamhg3 = pd.DataFrame(data)


k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 97
for i in trainGames["Radiant"]:
    j = trainGames["Dire"][l]
    if trainGames["Team Winner 2"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(trainGames["Team Winner 2"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 0
res = minimize(BTloglik, x0, method = 'nelder-mead')
res.x*(1/min(res.x))
data = {"Teams":Teamlist, "Ranks":res.x[:-1],"Draft Advantage 2":res.x[-1]}

Teamhg4 = pd.DataFrame(data)


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

  9.64861237 10.96179054 13.51346806 15.45596506 20.73162525 17.48103966]
[21.98199502 13.8632839  12.56686991 12.8222257  18.65260555 15.51424602
 11.5347004  16.29333729 14.56598797 16.66222191 16.96685581 20.31705693
  9.62037174 10.97444576 13.67435745 15.59304097 21.38671214 17.72740847]
[23.13317749 14.24256015 12.83509027 13.1418221  19.16823399 16.32765043
 13.43177309 17.1206021  15.89648447 17.30752759 18.17030551 21.50556398
  9.73431713 11.17438944 14.02731888 16.59629594 22.07795878 18.83033029]
[22.7740906  14.21738234 12.72060713 13.01506185 18.96048959 15.83920459
 12.01071086 16.69418948 15.10956885 16.55337764 17.42992698 20.9254615
  9.6201781  11.01262888 13.89477887 15.97993389 21.63907741 18.1616061 ]
[23.06760733 14.38307788 12.80072129 13.09310937 19.11920239 15.61418569
 11.75572693 16.68404982 14.91751372 16.381718   17.30520608 21.14922584
  9.55725795 10.94483444 13.97410203 15.87593339 21.63607202 18.03695135]
[23.18698172 14.18715249 12.82091228 13.1160857

[23.28073845 18.48523918 14.76612652 15.69540809 20.25125057 13.83060991
 10.67240357 17.73107364 13.91404683 12.77662737 12.25177219 21.54657101
  8.1313083   9.7233978  16.33252406 11.66928149 20.20131985 11.66785046]
[25.69635622 21.71323971 16.96608459 17.92419787 21.89452354 14.25632702
 12.52831931 19.83334715 13.94631557 11.39637309  9.86017051 23.43578469
  7.67212369  9.59312966 18.57537341 10.50721089 20.49012319  9.03188224]
[23.33191737 20.27073248 15.8847055  16.64189989 21.87851127 14.75422039
 14.31380503 19.44942343 18.50459112 11.87670428 11.38737168 22.42721578
  8.08029241  9.91564513 17.34624783 11.53636403 20.07175918 11.25390413]
[23.5438813  19.97935565 15.6564887  16.64668179 20.14263583 14.60810051
 12.6742744  19.38881807 17.12474099 12.75557582 11.61995246 22.51044384
  8.02713879  9.67651636 17.34587283 11.27532967 19.45467735 10.91548686]
[22.2887247  19.94368451 15.41861415 16.55752193 18.93126698 15.35383279
 13.08036466 19.70165471 18.6940859  13.1568706

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log



[15.26496028 16.29626505 12.47594323 14.04771389 13.82852171 11.97284281
 10.03586522 15.09083736 12.31600458 12.32484599 11.20141435 17.15022566
  7.71331842  8.82105014 14.41467027  7.95681427 13.52797012  8.81716195]
[17.63839409 18.47311729 13.92671773 15.53667654 15.63944179 12.37452134
 10.86870075 16.75765769 13.7120459  12.25009079 11.12789017 19.43416402
  7.62660116  9.08895068 16.02594463  8.19826428 15.34459874  8.94316632]
[16.75873845 17.5985956  13.33442224 14.95044916 14.71351335 12.21172472
 10.72339418 15.99513463 13.15604675 12.21597466 11.13724653 18.61615103
  7.65572756  8.97750967 15.413694    8.35499757 14.33764205  8.96474528]
[15.95123395 17.58315734 13.15800743 14.92155364 14.77727939 12.14290607
 10.56304758 15.89086082 12.40000477 12.70963683 11.41439474 18.44118237
  7.6291081   9.01070213 15.38012813  8.1578701  14.55560464  9.16635316]
[16.92046473 17.6901436  13.38079586 14.96273983 14.74595974 11.72010101
 10.7976316  16.04095912 13.95009594 12.536562

...

 6.14862485 6.11322564 6.0029356  6.14172607 5.98318501 6.1372846 ]
[5.88572297 6.12740784 6.12644586 6.01677652 6.00885773 6.10031749
 6.10423079 6.08533836 6.06034463 5.99083727 5.85151956 5.80900625
 6.15954979 6.12422636 6.00850225 6.15249249 5.99430713 6.14722182]
[5.89218083 6.13001257 6.12877247 6.01908657 6.00948589 6.10062084
 6.1073452  6.08586511 6.06164482 5.98987306 5.85987311 5.81283222
 6.16098731 6.12562843 6.01381082 6.15385476 5.99411233 6.1499592 ]
[5.87971775 6.11072599 6.11109398 6.00118271 5.99318981 6.08285949
 6.08800651 6.06936157 6.04756567 5.97396989 5.84184616 5.79588138
 6.14223459 6.10763501 5.9934549  6.13532486 5.98029967 6.13050068]
[5.88510692 6.12275412 6.12179411 6.0125475  6.005275   6.09419466
 6.1011142  6.08121773 6.05667073 5.98648129 5.85373939 5.80748506
 6.15381556 6.11836382 6.00866402 6.14670869 5.98409851 6.14282189]
[5.8886824  6.11911268 6.11947341 6.01055732 6.00204876 6.09046961
 6.09873613 6.07682788 6.05424708 5.97947397 5.85464041 5

 6.1661742  6.13093643 6.01520423 6.15782394 6.02485699 6.14045128]
[5.88735236 6.13759508 6.14129752 6.02287564 6.00227141 6.0973047
 6.12497517 6.0917183  6.07726998 5.99239066 5.87605935 5.82657126
 6.17281563 6.13723367 6.02601116 6.16411468 6.03375546 6.15005735]
[5.85928164 6.09627552 6.10051994 5.98390378 5.96952864 6.06239129
 6.09023784 6.04784414 6.03944418 5.95347435 5.82897493 5.78380381
 6.13260105 6.0963987  5.99392844 6.12457336 5.98675966 6.11008511]
[5.8630202  6.11934803 6.12172842 6.00260792 5.98457711 6.08208183
 6.10466735 6.07084714 6.0648493  5.98305844 5.85314705 5.80759392
 6.15328283 6.11762047 6.00612592 6.14467362 6.01620111 6.12884799]
[5.88633713 6.14106249 6.14044158 6.02440324 6.01174518 6.10067816
 6.12953608 6.09001124 6.07209549 5.99791625 5.87288537 5.82682756
 6.17332066 6.13557006 6.02804809 6.16530978 6.01870079 6.15058221]
[5.86811936 6.11628958 6.12053193 6.00123882 5.97986954 6.07801522
 6.10726153 6.06633461 6.05836938 5.96871695 5.85219601 5.

 5.75963686 5.71199761 5.65750934 5.7491764  5.67535239 5.74240584]
[5.42069353 5.644951   5.64857992 5.50184913 5.57971447 5.57802362
 5.61866941 5.58385868 5.586949   5.4812207  5.35351205 5.45398466
 5.675479   5.62832351 5.57822585 5.66544476 5.59460169 5.6617131 ]
[5.36116652 5.59565722 5.60280066 5.43894871 5.52128603 5.51802411
 5.55539583 5.53621164 5.5379879  5.45218862 5.28814965 5.41711363
 5.62871958 5.58132423 5.52477159 5.61753973 5.59099264 5.61102514]
[5.55323592 5.82270976 5.81824107 5.67562578 5.73802525 5.75673505
 5.78611473 5.7444249  5.7544927  5.67063979 5.52423458 5.60190186
 5.84869362 5.79952351 5.7430331  5.83634145 5.74012877 5.83362155]
[5.36407745 5.61545476 5.60668401 5.44631748 5.52861566 5.53538938
 5.55510108 5.53945048 5.55734917 5.45602077 5.29591073 5.4197913
 5.63583042 5.58838156 5.53097399 5.62597794 5.56709388 5.61773428]
[5.47297957 5.7291355  5.73743518 5.58511712 5.66194094 5.66791687
 5.70103024 5.67895875 5.67199821 5.61265545 5.39716535 5.

[5.21499367 5.48390486 5.47754607 5.33146398 5.41926542 5.41648084
 5.46583938 5.44449047 5.43901572 5.33404998 5.18609841 5.31448436
 5.50829752 5.4607151  5.41431185 5.50067569 5.42766127 5.49600598]
[5.17131014 5.43740276 5.42891934 5.28108383 5.37266875 5.36624287
 5.41524613 5.39362197 5.3885659  5.27436894 5.14638388 5.28184008
 5.4577958  5.41045393 5.3663155  5.4511645  5.38844533 5.44552752]
[5.19675962 5.47103793 5.46282786 5.31443225 5.40356599 5.40237617
 5.4468523  5.42935286 5.42151327 5.32291548 5.17139165 5.30580434
 5.49318319 5.44555759 5.39867288 5.48611379 5.41929237 5.48206048]
[5.19487346 5.47261117 5.46187356 5.31236185 5.40382264 5.39847843
 5.44720707 5.42455216 5.41889982 5.31439923 5.17788089 5.31285543
 5.49155309 5.44300364 5.40033164 5.48433396 5.41692788 5.47819545]
[5.18255298 5.44594928 5.43932059 5.29281523 5.38260663 5.37789315
 5.42655327 5.40603245 5.40068647 5.28816652 5.15257889 5.28526195
 5.46881372 5.42184611 5.37579344 5.46197358 5.39653849 5.

[5.18950963 5.46388241 5.45648844 5.31030545 5.39917632 5.3966209
 5.44250487 5.42285174 5.41674882 5.30221088 5.17244391 5.30729105
 5.48643767 5.43922615 5.39467356 5.47932431 5.41473284 5.47566122]
[5.18563174 5.46151516 5.45309524 5.30684907 5.39717148 5.39358001
 5.43998137 5.41937744 5.41366626 5.30069445 5.16633782 5.30329607
 5.48371245 5.43597499 5.39145205 5.4767604  5.40943868 5.47317113]
[5.18415147 5.45530522 5.44753387 5.30093335 5.3902049  5.3873954
 5.43374129 5.41325313 5.40738948 5.29291447 5.16350881 5.29836461
 5.47729482 5.43010061 5.38636412 5.47030102 5.40574095 5.4666149 ]
[5.18693972 5.4588288  5.45043677 5.30428224 5.39350432 5.39064405
 5.43692129 5.41571777 5.41065157 5.29400522 5.16667107 5.3013416
 5.48044991 5.43313556 5.38934554 5.47349733 5.40721626 5.46982644]
[5.18914389 5.46031139 5.45152319 5.30568859 5.39454742 5.39187333
 5.43806808 5.41621862 5.41186579 5.29270332 5.168827   5.30268916
 5.48151924 5.43425399 5.39064936 5.47459346 5.40750323 5.470

In [170]:
Teamhg3

Teams     Ranks  Draft Advantage 1
0                    OG  2.013910           2.142735
1           Team Liquid  1.343531           2.142735
2               PSG.LGD  1.569671           2.142735
3           Team Secret  1.868233           2.142735
4           Vici Gaming  1.592119           2.142735
5         Evil Geniuses  1.278382           2.142735
6   Royal Never Give Up  1.182304           2.142735
7       Infamous Gaming  1.305086           2.142735
8                Newbee  1.379038           2.142735
9          TNC Predator  1.433063           2.142735
10           Virtus.pro  1.187189           2.142735
11               Fnatic  1.303137           2.142735
12             Alliance  1.035370           2.142735
13              Mineski  1.202711           2.142735
14        Natus Vincere  2.176091           2.142735
15   Chaos Esports Club  1.047717           2.142735
16          KEEN GAMING  1.266254           2.142735
17    Ninjas in Pyjamas  1.109520           2.142735

In [180]:
testTeamskill1 = np.zeros(m)
testTeamskill2 = np.zeros(m)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1

testTeamskill3 = np.zeros(m)
testTeamskill4 = np.zeros(m)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    
testTeamwin1 = np.zeros(m)
for i in range(m):
    prob = testTeamskill1[i]/(testTeamskill1[i]+testTeamskill2[i])
    if prob >= 0.5:
        testTeamwin1[i] = 1    

testTeamwin2 = np.zeros(m)
for i in range(m):
    if testTeamskill3[i]>(testTeamskill4[i]):
        testTeamwin2[i] = 1

testGames["Team Winner"] = trainTeamwin1
testGames["Team Winner 2"] = trainTeamwin2


wins = 0
for i in range(len(testGames["Radiant"])-1):
    li = Teamhg3["Ranks"][index_dict[testGames["Radiant"][i]]]
    lj = Teamhg3["Ranks"][index_dict[testGames["Dire"][i]]]
    result = testGames["Winner"][i]
    if testGames["Team Winner"][i]== 1:
        """Radiant is home team"""
        pi = Teamhg3["Draft Advantage 1"][0]*li/(Teamhg3["Draft Advantage 1"][0]*li + lj)
    elif 0 == testGames["Team Winner"][i]:
        """Dire is home team"""
        pi = li/(Teamhg3["Draft Advantage 1"][0]*lj + li)        

    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy4 = wins/len(testGames["Radiant"])
test_accuracy4

51


0.53125

In [181]:
wins = 0
for i in range(len(testGames["Radiant"])-1):
    li = Teamhg4["Ranks"][index_dict[testGames["Radiant"][i]]]
    lj = Teamhg4["Ranks"][index_dict[testGames["Dire"][i]]]
    result = testGames["Winner"][i]
    if testGames["Team Winner"][i]== 1:
        """Radiant is home team"""
        pi = Teamhg4["Draft Advantage 2"][0]*li/(Teamhg4["Draft Advantage 2"][0]*li + lj)
    elif 0 == testGames["Team Winner"][i]:
        """Dire is home team"""
        pi = li/(Teamhg4["Draft Advantage 2"][0]*lj + li)        

    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy5 = wins/len(testGames["Radiant"])
test_accuracy5

44


0.4583333333333333

In [182]:
test2.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [58]:
test2

Teams                   Ranks
0                    OG      [2.25569281109922]
2               PSG.LGD    [1.8909255343557532]
3           Team Secret    [1.2833834586072261]
1           Team Liquid    [1.2128625066173264]
4           Vici Gaming    [0.8680274464421075]
5         Evil Geniuses    [0.7536658535368154]
13              Mineski    [0.7093699957729003]
9          TNC Predator    [0.6354337537038568]
8                Newbee    [0.6237124619241472]
12             Alliance   [0.49697482060111675]
7       Infamous Gaming    [0.2584829093573106]
6   Royal Never Give Up   [0.12056848452335495]
11               Fnatic   [0.04995648152497397]
10           Virtus.pro   [0.04881648194085936]
14        Natus Vincere   [0.02457553418378923]
16          KEEN GAMING  [-0.24346696071855753]
15   Chaos Esports Club   [-0.7531475058296778]
17    Ninjas in Pyjamas    [-1.000884034807416]

In [59]:
test_accuracy1

0.5104166666666666

In [60]:
test4.sort_values(by=['Ranks'], inplace=True, ascending=False)

#### 

In [61]:
test4[:18]

Teams                 Ranks
75      Winter Wyvern  [2.8722942774938094]
18          Dark Seer    [2.13178354297329]
37         Windranger   [2.014505006985294]
21             Tinker  [2.0061420089022968]
0                  Io  [1.9845330465000255]
102  Treant Protector  [1.9789100223453826]
111     Night Stalker  [1.9643365514106212]
13               Chen  [1.7442928850054995]
14              Meepo  [1.6517315407171256]
78        Monkey King  [1.5922865882777966]
8    Templar Assassin   [1.576116733849483]
97            Slardar  [1.5076230374834194]
2             Abaddon  [1.4118088718005402]
16      Faceless Void  [1.3682835460924003]
40             Medusa  [1.3549611737493343]
6          Tidehunter  [1.3280406766518225]
86      Skywrath Mage  [1.2929663838904737]
4          Gyrocopter   [1.282413943024915]

In [62]:
Teamhg4

Teams  Ranks  Draft Advantage 1
0                    OG    inf                inf
1           Team Liquid    inf                inf
2               PSG.LGD    inf                inf
3           Team Secret    inf                inf
4           Vici Gaming    inf                inf
5         Evil Geniuses    inf                inf
6   Royal Never Give Up    inf                inf
7       Infamous Gaming    inf                inf
8                Newbee    inf                inf
9          TNC Predator    inf                inf
10           Virtus.pro    inf                inf
11               Fnatic    inf                inf
12             Alliance    inf                inf
13              Mineski    inf                inf
14        Natus Vincere    inf                inf
15   Chaos Esports Club    inf                inf
16          KEEN GAMING    inf                inf
17    Ninjas in Pyjamas    inf                inf

In [63]:
test5.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [64]:
test5[:18]

Heroes     Ranks
11      Lifestealer  0.035506
7         Ogre Magi  0.030471
4        Gyrocopter  0.022834
27          Leshrac  0.022082
54             Lina  0.019356
19             Sven  0.018910
69       Grimstroke  0.017746
20           Mirana  0.017610
38   Crystal Maiden  0.017458
68      Beastmaster  0.016626
65            Slark  0.015959
49      Enchantress  0.015732
41     Ember Spirit  0.015706
10    Shadow Shaman  0.014632
30        Sand King  0.014616
104       Disruptor  0.014434
100      Lone Druid  0.014311
43         Silencer  0.014216

In [65]:
test_accuracy3

0.5520833333333334

In [66]:
Teamhg

Teams     Ranks  Radiant Advantage
0                    OG  1.506624           2.497178
1           Team Liquid  1.432192           2.497178
14        Natus Vincere  1.426334           2.497178
3           Team Secret  1.362046           2.497178
4           Vici Gaming  1.359377           2.497178
2               PSG.LGD  1.284708           2.497178
13              Mineski  1.279778           2.497178
8                Newbee  1.273076           2.497178
6   Royal Never Give Up  1.239052           2.497178
5         Evil Geniuses  1.214277           2.497178
9          TNC Predator  1.200856           2.497178
11               Fnatic  1.185388           2.497178
7       Infamous Gaming  1.152014           2.497178
16          KEEN GAMING  1.141608           2.497178
10           Virtus.pro  1.115553           2.497178
17    Ninjas in Pyjamas  1.071906           2.497178
15   Chaos Esports Club  1.054776           2.497178
12             Alliance  1.022962           2.497178

In [67]:
Teamhg2

Teams     Ranks  Draft Advantage 1
1           Team Liquid  1.816846            2.81559
0                    OG  1.668254            2.81559
2               PSG.LGD  1.554393            2.81559
3           Team Secret  1.482552            2.81559
4           Vici Gaming  1.355827            2.81559
9          TNC Predator  1.307689            2.81559
14        Natus Vincere  1.299229            2.81559
6   Royal Never Give Up  1.298073            2.81559
13              Mineski  1.294230            2.81559
11               Fnatic  1.264359            2.81559
8                Newbee  1.257147            2.81559
5         Evil Geniuses  1.225424            2.81559
7       Infamous Gaming  1.192766            2.81559
10           Virtus.pro  1.185506            2.81559
16          KEEN GAMING  1.123247            2.81559
17    Ninjas in Pyjamas  1.093704            2.81559
15   Chaos Esports Club  1.063794            2.81559
12             Alliance  1.026703            2.81559

In [68]:
test_accuracy4

0.0

In [69]:
test_accuracy5

0.3333333333333333

In [70]:
teamhg3

NameError: name 'teamhg3' is not defined

In [ ]:
Teamhg3

In [ ]:
testGames

In [ ]:
testHeroes1

In [ ]:
Teamhg3

Need to do some testing against coin-flip

96